### Imports

In [1]:
import pandas as pd
from datetime import timedelta
from datetime import datetime as dt
import datetime
import yfinance as yf
import numpy as np
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.model_selection import train_test_split, cross_val_score, StratifiedKFold
from sklearn.metrics import accuracy_score, classification_report
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from imblearn.over_sampling import SMOTE
from sklearn.model_selection import RandomizedSearchCV
from imblearn.over_sampling import ADASYN
from xgboost import XGBClassifier
import xgboost as xgb
import pytz
from sklearn.preprocessing import MinMaxScaler
from imblearn.over_sampling import BorderlineSMOTE
from sklearn.decomposition import PCA
from sklearn.metrics import roc_auc_score
from sklearn.feature_selection import SelectFromModel
import tensorflow as tf
from tensorflow import keras
from keras import layers, callbacks
from sklearn.utils.class_weight import compute_class_weight
from sklearn.base import BaseEstimator, ClassifierMixin
from sklearn.pipeline import Pipeline
from tensorflow.keras.optimizers.legacy import Adam
from tensorflow.keras.layers import Dense, BatchNormalization, Dropout
from tensorflow.keras.regularizers import l2
from sklearn.ensemble import VotingClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.tree import DecisionTreeClassifier
from keras.models import Sequential
import keras_tuner as kt
from kerastuner.tuners import RandomSearch
import joblib
import itertools
import lightgbm as lgb

/var/folders/zc/z8rbpqpj3s38f0x8wmhkq0lh0000gn/T/ipykernel_19412/3810277901.py:39: DeprecationWarning: `import kerastuner` is deprecated, please use `import keras_tuner`.
  from kerastuner.tuners import RandomSearch


### Helper Functions

In [2]:
def next_four_fridays():
    # Get today's date and time in EST timezone
    est = pytz.timezone('US/Eastern')
    today = dt.now(est)
    
    # Find the next Friday
    days_until_friday = (4 - today.weekday() + 7) % 7
    next_friday = today + timedelta(days=days_until_friday)
    
    # Reset the time to 4:30 PM on the next Friday
    next_friday = next_friday.replace(hour=16, minute=30, second=0, microsecond=0)
    
    # If today is Friday and it's past 4:30 PM, consider the next week's Friday
    if today.weekday() == 4 and today.time() > next_friday.time():
        next_friday += timedelta(days=7)
    
    # Remove time from datetime for output
    next_friday = next_friday.date()
    
    # Find the Friday after the next
    following_friday = next_friday + timedelta(days=7)
    
    # Find the Friday after the following
    next_next_friday = following_friday + timedelta(days=7)
    
    # Find the Friday after the next next
    next_next_next_friday = next_next_friday + timedelta(days=7)
    
    return next_friday.strftime('%Y-%m-%d'), following_friday.strftime('%Y-%m-%d'), next_next_friday.strftime('%Y-%m-%d'), next_next_next_friday.strftime('%Y-%m-%d')

# Get the next four Fridays
friday1, friday2, friday3, friday4 = next_four_fridays()
print(f"The next four Fridays are: {friday1}, {friday2}, {friday3}, and {friday4}")

The next four Fridays are: 2024-03-15, 2024-03-22, 2024-03-29, and 2024-04-05


# Viewing option chains

In [3]:
print(friday1)

2024-03-15


In [4]:
file_viewer = pd.read_csv('Data/naked_puts_results.csv')
filtered_data = file_viewer[file_viewer['Expiration Date'] == friday1]

# Display all rows, no limit
pd.set_option('display.max_rows', None)
# Display all columns, no limit
pd.set_option('display.max_columns', None)

filtered_data['ROI (%)'] = filtered_data['ROI (%)'].astype(float)
# filter out rows with ROI (%) greater than 0.8
# filtered_data = filtered_data[filtered_data['ROI (%)'] > 0.8]
# filter out rows with strike price less than 6
# filtered_data = filtered_data[filtered_data['strike'] <= 7]

# sort by ROI (%) in ascending order
filtered_data = filtered_data.sort_values(by=['ROI (%)'], ascending=False)

# Show only the columns 'Expiration Date', 'ETF', 'Stock Price', 'bid', 'strike', 'ROI (%)', 'OTM (%)', 'Implied Volatility', 'volume', 'openInterest', 'highPrice', 'Original Stock Price', 'Original ROI (%)', 'Original OTM (%)', '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP', '52WeekHigh', and '52WeekLow'
filtered_data = filtered_data[['Expiration Date', 'ETF', 'Stock Price', 'bid', 'strike', 'ROI (%)', 'OTM (%)', 'Implied Volatility', 'volume', 'openInterest', 'highPrice', 'Original Stock Price', 'Original ROI (%)',
    'Original OTM (%)', '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP', '52WeekHigh', '52WeekLow']]

# Show only the top 10 rows
filtered_data.head(20)

Expiration Date   ETF  Stock Price    bid  strike  ROI (%)  OTM (%)  \
2101      2024-03-15  CRIS        10.50   4.00     5.0   400.00    52.38   
2802      2024-03-15  EGIO         8.66   1.95     2.5   354.55    71.13   
3521      2024-03-15  GOEV         2.13   0.75     1.0   300.00    53.05   
3101      2024-03-15  FATH         4.43   1.75     2.5   233.33    43.57   
7215      2024-03-15  SNCR        10.84   1.25     2.5   100.00    76.94   
114       2024-03-15   ACB         3.18   0.73     1.5    94.81    52.83   
113       2024-03-15   ACB         3.18   0.42     1.0    72.41    68.55   
2742      2024-03-15    DY       142.83  37.00   135.0    37.76     5.48   
1936      2024-03-15   CNS        75.55  14.10    75.0    23.15     0.73   
6482      2024-03-15  PTCT        31.16   5.50    31.0    21.57     0.51   
1365      2024-03-15   BVN        16.24   1.75    10.0    21.21    38.42   
3427      2024-03-15  GERN         2.25   0.30     2.0    17.65    11.11   
5963      2024-03-15  OCEA         5.56   0.65     5.0    14.94    10.07   
5213      2024-03-15  MRUS        46.55   3.10    25.0    14.16    46.29   
4930      2024-03-15  MDGL       255.32  30.30   250.0    13.79     2.08   
1062      2024-03-15   BDC        89.66   9.00    80.0    12.68    10.77   
3007      2024-03-15   EVR       196.33  15.60   140.0    12.54    28.69   
4929      2024-03-15  MDGL       255.32  26.20   240.0    12.25     6.00   
4928      2024-03-15  MDGL       255.32  25.00   230.0    12.20     9.92   
3598      2024-03-15  GRPN        18.98   1.95    18.5    11.78     2.53   

      Implied Volatility  volume  openInterest  highPrice  \
2101               26.84     NaN          20.0       4.00   
2802               24.47     1.0           0.0       1.95   
3521               24.75     NaN           1.0       0.75   
3101                0.00     NaN           1.0       1.75   
7215               19.66     1.0         100.0       1.25   
114                 0.00    30.0          48.0       0.73   
113                 0.00    20.0         531.0       0.42   
2742                5.73     NaN           0.0      37.00   
1936                4.09   100.0           1.0      14.10   
6482                3.58     2.0           2.0       5.50   
1365                6.18    80.0          80.0       1.75   
3427                4.02  2743.0       11576.0       0.30   
5963                3.57   795.0         618.0       0.65   
5213                6.12     NaN           3.0       3.10   
4930                2.60     5.0         371.0      30.30   
1062                3.36     3.0           0.0       9.00   
3007                4.28     NaN          37.0      15.60   
4929                2.70     9.0         144.0      26.20   
4928                2.91   101.0         219.0      25.00   
3598                2.19    17.0          61.0       1.95   

      Original Stock Price  Original ROI (%)  Original OTM (%)  50-day MA  \
2101                 10.50            400.00             52.38      11.01   
2802                  8.66            354.55             71.13      10.11   
3521                  2.13            300.00             53.05       3.80   
3101                  4.43            233.33             43.57       4.43   
7215                 10.84            100.00             76.94       7.44   
114                   3.18             94.81             52.83       3.97   
113                   3.18             72.41             68.55       3.97   
2742                142.83             37.76              5.48     117.56   
1936                 75.55             23.15              0.73      71.14   
6482                 31.16             21.57              0.51      27.58   
1365                 16.24             21.21             38.42      15.18   
3427                  2.25             17.65             11.11       2.04   
5963                  5.56             14.94             10.07       1.16   
5213                 46.55             14.16    

In [11]:
# Read in data
df = pd.read_csv('Data/putsDataSuccessFailed.csv')

# Ensure 'Expiration Date' is in datetime format
df['Expiration Date'] = pd.to_datetime(df['Expiration Date'])


df = df[df['Expiration Date'] == '2024-03-08']

# Filter columns to keep
columns = ['Expiration Date', 'ETF', 'Original Stock Price', 'Stock Price', 'strike', 'volume',  
           'openInterest', 'highPrice', 'Original ROI (%)', 'Original OTM (%)',
           '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP',
           '52WeekHigh', '52WeekLow', 'Status']

df = df[columns]

# Take top 100 rows ordered by Original ROI (%)
df = df.sort_values('Original ROI (%)', ascending=False).head(100)

# Define function to color rows 
def color_row(row):
    color = 'lightgreen' if row['Status'] == 'Success' else 'lightcoral'
    return ['background-color: %s' % color]*len(row)

# Style DataFrame 
styled_df = (df.style  
             .applymap(lambda x: 'color: black') # Set text color
             .apply(color_row, axis=1) # Set row colors
             .format('{:.2f}', subset=df.select_dtypes(include=['float64']).columns))

# Display DataFrame 
styled_df


In [12]:
# Load the CSV file into a DataFrame
from sklearn.impute import SimpleImputer


df = pd.read_csv('Data/putsDataSuccessFailed.csv')

# Save the columns to be dropped for later use
retained_columns = df[['contractSymbol', 'Expiration Date', 'ETF']]

# Data Preprocessing
df.drop(['contractSymbol', 'Expiration Date', 'ETF'], axis=1, inplace=True)
df = pd.get_dummies(df, columns=['recommendationKey'], drop_first=True)

# Handle missing values with imputation
imputer = SimpleImputer(strategy='mean')
X = df.drop('Status', axis=1)
y = df['Status']

# Encode the target variable 'Status'
label_encoder = LabelEncoder()
y_encoded = label_encoder.fit_transform(y)

X_imputed = imputer.fit_transform(X)

# Address class imbalance with SMOTE
smote = SMOTE(random_state=42)
X_resampled, y_resampled = smote.fit_resample(X_imputed, y_encoded)

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X_resampled, y_resampled, test_size=0.2, random_state=42)

# Model Selection and Hyperparameter Tuning (LightGBM)
param_grid = {
    'n_estimators': [100, 200, 300],
    'max_depth': [3, 4, 5],
    'learning_rate': [0.05, 0.1, 0.2]
}

# Use GridSearchCV for hyperparameter tuning
lgb_classifier = lgb.LGBMClassifier(random_state=42)
grid_search = GridSearchCV(lgb_classifier, param_grid, cv=10, scoring='accuracy', n_jobs=-1)
grid_search.fit(X_train, y_train)

best_lgb_model = grid_search.best_estimator_

# Save the best model and other objects
joblib.dump(best_lgb_model, 'best_lgb_model.joblib')
joblib.dump(label_encoder, 'label_encoder.joblib')
joblib.dump(imputer, 'imputer.joblib')

# Load new data
new_data = pd.read_csv('Data/naked_puts_results.csv')

# Save the columns to be dropped from new data for later use
new_retained_columns = new_data[['contractSymbol', 'Expiration Date', 'ETF']]

# Preprocess new data as per training data
new_data.drop(['contractSymbol', 'Expiration Date', 'ETF'], axis=1, inplace=True)
new_data_encoded = pd.get_dummies(new_data, columns=['recommendationKey'], drop_first=True)

# Align columns of new data with training data
missing_cols = set(X.columns) - set(new_data_encoded.columns)
extra_cols = set(new_data_encoded.columns) - set(X.columns)
for c in missing_cols:
    new_data_encoded[c] = 0
new_data_encoded.drop(extra_cols, axis=1, inplace=True)
new_data_encoded = new_data_encoded[X.columns]

# Impute missing values
new_data_imputed = joblib.load('imputer.joblib').transform(new_data_encoded)

# Load the saved model and make predictions
loaded_model = joblib.load('best_lgb_model.joblib')
new_predictions = loaded_model.predict(new_data_imputed)

# Add predictions to the new data
new_data_with_predictions = new_data_encoded.copy()
new_data_with_predictions['Guess'] = joblib.load('label_encoder.joblib').inverse_transform(new_predictions)

# Reverse one-hot encoding to get original 'recommendationKey' column
def reverse_one_hot(df, original_column_prefix):
    one_hot_cols = [col for col in df if col.startswith(original_column_prefix)]
    df[original_column_prefix] = df[one_hot_cols].idxmax(axis=1).str.replace(original_column_prefix + '_', '')
    df.drop(one_hot_cols, axis=1, inplace=True)
    return df

new_data_with_predictions = reverse_one_hot(new_data_with_predictions, 'recommendationKey')

# Add back the retained columns to the new data with predictions
new_data_with_predictions = pd.concat([new_retained_columns.reset_index(drop=True), new_data_with_predictions.reset_index(drop=True)], axis=1)

# Save the new data with predictions
new_data_with_predictions.to_csv('Data/new_data_with_predictions.csv', index=False)

# Model Evaluation
y_pred = best_lgb_model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
report = classification_report(y_test, y_pred)

print(f'Best LightGBM Model: {best_lgb_model}')
print(f'Accuracy: {accuracy}')
print(report)

[LightGBM] [Info] Number of positive: 3672, number of negative: 3720
[LightGBM] [Info] Number of positive: 3672, number of negative: 3721
[LightGBM] [Info] Number of positive: 3672, number of negative: 3721
[LightGBM] [Info] Number of positive: 3672, number of negative: 3721
[LightGBM] [Info] Number of positive: 3672, number of negative: 3721
[LightGBM] [Info] Number of positive: 3672, number of negative: 3721
[LightGBM] [Info] Number of positive: 3672, number of negative: 3721
[LightGBM] [Info] Number of positive: 3672, number of negative: 3720
[LightGBM] [Info] Number of positive: 3672, number of negative: 3720
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.004928 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.005303 seconds.
You can set `force_row_wise=true` to remove the o

In [13]:
# Read in data 
df = pd.read_csv('Data/new_data_with_predictions.csv')

# Sort by Original ROI column  
df = df.sort_values(by='Original ROI (%)', ascending=False)  

# Filter to top 300 rows
df = df.head(300)

# Filter columns to show
columns = ['Expiration Date', 'ETF', 'Stock Price', 'bid', 'strike', 
           'ROI (%)', 'OTM (%)', 'recommendationKey', 'targetLowPrice', 'targetMeanPrice', 'targetHighPrice', 'Guess']
df = df[columns]

# Define row color function
def color_row(row):
    color = 'lightgreen' if row['Guess'] == 'Success' else 'lightcoral'
    return ['background-color: %s' % color]*len(row)

# Apply cell and row styling
styled_df = (df.style
                .applymap(lambda x: 'color: black') # Black text
                .apply(color_row, axis=1) # Color rows
                .format('{:.2f}', subset=df.select_dtypes(include=['float64']).columns)) 

# Display styled DataFrame
styled_df